In [1]:
%%capture
!pip install import_ipynb --no-cache
import import_ipynb
m = __import__("Methods")

In [2]:
import pandas as pd
pd.set_option('display.max_columns', None)
import matplotlib.pyplot as plt
from urllib.request import urlretrieve
from sklearn.preprocessing import StandardScaler
import numpy as np
from scipy.stats import boxcox
import pandas as pd
import zipfile
import urllib.request
import os

In [3]:
rna_seq = dict()
phenotype = dict()
meta = dict()

# RR-1 Data

In [4]:
# Dataset identifiers
datasets = ["47", "48", "137", "168"]

# --- Load Metadata ---
for ds in datasets:
    meta_path = f"../meta_data/OSD-{ds}_metadata_OSD-{ds}-ISA/s_OSD-{ds}.txt"
    if os.path.exists(meta_path):
        print(f"Loading metadata for OSD-{ds}...")
        meta[ds] = pd.read_csv(meta_path, sep="\t", header=0)

# --- Load RNA-seq Data ---
for ds in datasets:
    rna_path = f"../raw_data/GLDS-{ds}_rna_seq_Normalized_Counts.csv"
    if os.path.exists(rna_path):
        print(f"Loading RNA-seq data for OSD-{ds}...")
        rna_seq[ds] = pd.read_csv(rna_path)

# --- Load Phenotype Data ---
pheno_sources = {
    "47": "LSDS-29_Histology_OSD_47_Histology_TRANSFORMED.csv",
    "48": "LSDS-2_Histology_OSD_48_Histology_TRANSFORMED.csv",
    "137": "LSDS-28_Histology_OSD_137_Histology_TRANSFORMED.csv"
}

for ds, fname in pheno_sources.items():
    pheno_path = f"../raw_data/{fname}"
    if os.path.exists(pheno_path):
        print(f"Loading phenotype data for OSD-{ds}...")
        phenotype[ds] = pd.read_csv(pheno_path)

# --- Filter RNA-seq Data ---
for ds in rna_seq:
    print(f"Filtering RNA-seq data for OSD-{ds}...")

    df = rna_seq[ds].copy()

    if ds == "168":
        # Convert index to 'Unnamed: 0' column for compatibility with filter_data
        df = df.reset_index().rename(columns={"index": "Unnamed: 0"})

    rna_seq[ds] = m.filter_data(df, dropnans=True, dropgenes=True, droplowcvs=0.5, droplowcount=10)


# --- Transpose RNA-seq Data ---
for ds in rna_seq:
    print(f"Transposing RNA-seq data for OSD-{ds}...")
    rna_seq[ds] = m.transpose_df(rna_seq[ds], cur_index_col="Unnamed: 0", new_index_col="Sample name")


# --- Align RNA-seq and Phenotype by Common Samples (47, 48) ---
for ds in ["47", "48", "137"]:
    if ds in rna_seq and ds in phenotype:
        print(f"Aligning RNA-seq and phenotype data for OSD-{ds}...")
        rna = rna_seq[ds]
        pheno = phenotype[ds]

        common = set(rna["Sample name"]) & set(pheno["Sample name"])
        rna_common = rna[rna["Sample name"].isin(common)].copy()
        pheno_common = pheno[pheno["Sample name"].isin(common)].copy()
        pheno_common = pheno_common[["Sample name", "ORO Positivity (%)"]]

        rna_common.reset_index(drop=True, inplace=True)
        pheno_common.reset_index(drop=True, inplace=True)

        print(f"Saving aligned data for OSD-{ds}...")
        rna_common.to_csv(f"../x_variables/rna_seq-{ds}.csv", index=False)
        pheno_common.to_csv(f"../y_variables/pheno-{ds}.csv", index=False)

# --- Special Case: phenotype["137"] aligned with rna_seq["168"] ---
if "168" in rna_seq and "137" in phenotype:
    print("Aligning RNA-seq data from OSD-168 with phenotype data from OSD-137...")
    rna = rna_seq["168"]
    pheno = phenotype["137"]

    common = set(rna["Sample name"]) & set(pheno["Sample name"])
    rna_common = rna[rna["Sample name"].isin(common)].copy()
    pheno_common = pheno[pheno["Sample name"].isin(common)].copy()
    pheno_common = pheno_common[["Sample name", "ORO Positivity (%)"]]

    rna_common.reset_index(drop=True, inplace=True)
    pheno_common.reset_index(drop=True, inplace=True)

    print("Saving aligned data for OSD-168 (RNA) and OSD-137 (phenotype)...")
    rna_common.to_csv("../x_variables/rna_seq-168.csv", index=False)
    pheno_common.to_csv("../y_variables/pheno-168.csv", index=False)


Loading metadata for OSD-47...
Loading metadata for OSD-48...
Loading metadata for OSD-137...
Loading metadata for OSD-168...
Loading RNA-seq data for OSD-47...
Loading RNA-seq data for OSD-48...
Loading RNA-seq data for OSD-137...
Loading RNA-seq data for OSD-168...
Loading phenotype data for OSD-47...
Loading phenotype data for OSD-48...
Loading phenotype data for OSD-137...
Filtering RNA-seq data for OSD-47...
Number of protein coding genes: 15059
2520
Filtering RNA-seq data for OSD-48...
Number of protein coding genes: 15991
5244
Filtering RNA-seq data for OSD-137...
Number of protein coding genes: 15567
3004
Filtering RNA-seq data for OSD-168...
Number of protein coding genes: 18551
6661
Transposing RNA-seq data for OSD-47...
Transposing RNA-seq data for OSD-48...
Transposing RNA-seq data for OSD-137...
Transposing RNA-seq data for OSD-168...
Aligning RNA-seq and phenotype data for OSD-47...
Saving aligned data for OSD-47...
Aligning RNA-seq and phenotype data for OSD-48...
Saving

In [5]:
rna_seq["47"]

Sample name  ENSMUSG00000000094  ENSMUSG00000000204  \
0  Mmus_C57-6T_LVR_BSL_Rep1_B1            2.976790           13.364248   
1  Mmus_C57-6T_LVR_BSL_Rep2_B2            0.000000           23.217468   
2  Mmus_C57-6T_LVR_BSL_Rep3_B3            4.184136           35.707730   
3   Mmus_C57-6T_LVR_GC_Rep1_G2            0.000000           20.428429   
4   Mmus_C57-6T_LVR_GC_Rep2_G3            0.000000           38.962512   
5   Mmus_C57-6T_LVR_GC_Rep3_G5            3.665464           39.162227   
6  Mmus_C57-6T_LVR_FLT_Rep1_F1            0.000000           48.619383   
7  Mmus_C57-6T_LVR_FLT_Rep2_F2            2.254113            1.068710   
8  Mmus_C57-6T_LVR_FLT_Rep3_F4            3.902494           17.581430   

   ENSMUSG00000000248  ENSMUSG00000000359  ENSMUSG00000000365  \
0            0.000000           13.293231            0.000000   
1            6.762921            7.167388            3.716503   
2            2.542337           28.303944            7.202477   
3            0.000000           37.322612            0.000000   
4            1.986741           32.137948            6.221168   
5            4.293901           23.695221            3.122388   
6            3.627302           10.416046            0.000000   
7            0.753928            8.326734           11.013757   
8            0.000000           17.225656            0.368922   

   ENSMUSG00000000402  ENSMUSG00000000409  ENSMUSG00000000416  \
0            3.113837          101.252292            8.321191   
1            0.951380          160.186783            9.696798   
2            1.025815           94.794757            7.115434   
3            0.000000           66.559352           11.822939   
4            3.883461          105.224394           54.709471   
5            0.000000          206.827573           13.333192   
6            0.000000           59.802097           14.947693   
7            1.105271           39.349749            4.982041   
8            3.827060           38.113735            6.183500   

   ENSMUSG00000000562  ENSMUSG00000000617  ENSMUSG00000000627  \
0            1.331374            0.000000            1.565405   
1            3.661008            2.186775           10.466050   
2            1.315814            1.024151            0.773555   
3            1.588528            1.004431           10.343451   
4            0.902846            1.938582            2.928471   
5            1.152704            6.198091            3.388319   
6            1.375636            0.815034            2.406001   
7            0.000000            0.000000            2.500418   
8            0.000000            0.733211            0.000000   

   ENSMUSG00000000628  ENSMUSG00000000732  ENSMUSG00000000794  \
0          112.043023           47.920803            0.000000   
1           70.139399           61.885396            2.472985   
2           63.782714           68.772802            1.777646   
3          162.998697           53.292361            0.871708   
4           75.823845           50.835827            3.364846   
5          146.702606          150.266665            0.778643   
6          200.508147           58.355272            0.000000   
7           22.721781           35.589407            9.413954   
8           36.624757           36.777145            0.828997   

   ENSMUSG00000000861  ENSMUSG00000000903  ENSMUSG00000000982  \
0           30.581573           31.544484            2.075896   
1           31.505935           21.452055            8.562437   
2           17.637745           64.362977            3.077451   
3           16.649393           32.962301            5.030323   
4           14.331501           11.421611            8.737806   
5           74.021512           12.479410           21.567730   
6           30.819387            4.170611           11.698930   
7           16.607513           13.002665            3.315786   
8            8.167948            4.689837            2.870273   

   ENSMUSG00000000983  

In [6]:
rna_seq["48"]

Sample name  ENSMUSG00000000037  ENSMUSG00000000058  \
0    Mmus_C57-6J_LVR_GC_I_Rep1_M31            0.719385          113.448170   
1    Mmus_C57-6J_LVR_GC_I_Rep2_M32            0.778113          225.702439   
2   Mmus_C57-6J_LVR_FLT_I_Rep1_M21            1.483671          243.480317   
3   Mmus_C57-6J_LVR_FLT_I_Rep2_M22            0.740563           46.269676   
4    Mmus_C57-6J_LVR_GC_C_Rep1_M36           12.577856           68.694512   
5    Mmus_C57-6J_LVR_GC_C_Rep2_M37            0.590956           33.423183   
6    Mmus_C57-6J_LVR_GC_C_Rep3_M38            0.000000           54.486926   
7    Mmus_C57-6J_LVR_GC_C_Rep4_M39            4.962914           50.902051   
8    Mmus_C57-6J_LVR_GC_C_Rep5_M40            0.876631           48.208941   
9   Mmus_C57-6J_LVR_FLT_C_Rep1_M25            0.000000           47.974016   
10  Mmus_C57-6J_LVR_FLT_C_Rep2_M26            0.000000           58.755443   
11  Mmus_C57-6J_LVR_FLT_C_Rep3_M27            1.244119           43.520189   
12  Mmus_C57-6J_LVR_FLT_C_Rep4_M28           11.764465           26.132422   
13  Mmus_C57-6J_LVR_FLT_C_Rep5_M30            2.028844           26.460150   

    ENSMUSG00000000094  ENSMUSG00000000120  ENSMUSG00000000126  \
0             4.200428          199.811035           10.778718   
1             6.680560          189.397285           38.752921   
2             0.576261          261.610831           20.474522   
3             2.101066          117.156739            3.110499   
4             1.193612           82.459491            2.356079   
5             1.147632           53.232844            2.265345   
6             0.000000           73.799890            6.946148   
7             0.000000           74.370508           11.156155   
8             0.000000           46.474632            6.062242   
9             1.331660           86.739467           14.457106   
10            0.000000           50.336259            3.511960   
11            0.000000           63.187821            7.153644   
12            0.000000           43.483666            3.181848   
13            2.626674           25.923022            9.073362   

    ENSMUSG00000000183  ENSMUSG00000000184  ENSMUSG00000000197  \
0             0.000000          455.561415            0.000000   
1            19.387095          452.669319            0.465764   
2             2.274873         1908.500151           34.813704   
3             0.000000          617.504347            0.000000   
4             1.177993          241.828071            4.609110   
5             1.132614          234.642445            0.707472   
6             1.736468          397.532407            0.000000   
7             0.000000          463.570086            0.000000   
8             0.000000          294.750080            1.262164   
9             0.000000          290.199758            0.000000   
10            0.000000          314.090543            0.000000   
11            0.000000          391.197686            0.000000   
12            0.000000          264.251583            0.662476   
13            0.000000          161.748246            0.000000   

    ENSMUSG00000000204  ENSMUSG00000000214  ENSMUSG00000000223  \
0             8.046715            0.000000            0.000000   
1             1.484579            2.683445           22.090131   
2             3.275181          923.096995            5.274310   
3             7.043737            5.372373            0.000000   
4            23.511928            0.000000            0.757991   
5            14.567599            0.000000            3.776177   
6            52.279319            0.000000            0.000000   
7            52.330538            0.000000            0.000000   
8            16.498847            0.000000            0.000000   
9            43.351439            0.000000            0.000000   
10          277.697000            0.000000            1.229779   
11           70.370864            2.565758            4.602891   
12          

In [7]:
# --- Identify common genes across all RNA-seq datasets ---
print("Identifying common genes across datasets...")
common_genes = None

for ds, df in rna_seq.items():
    gene_columns = set(df.columns) - {"Sample name"}  # exclude metadata column
    if common_genes is None:
        common_genes = gene_columns
    else:
        common_genes &= gene_columns  # intersection

common_genes = sorted(list(common_genes))  # sort for consistent order

print(f"Number of common genes across datasets: {len(common_genes)}")

# --- Subset each RNA-seq dataset to common genes and concatenate ---
rna_combined = []

for ds, df in rna_seq.items():
    print(f"Subsetting and appending OSD-{ds}...")
    subset = df[["Sample name"] + common_genes].copy()
    subset["Dataset"] = f"OSD-{ds}"  # optional: track source
    rna_combined.append(subset)

# Combine all into a single DataFrame
rna_all = pd.concat(rna_combined, axis=0, ignore_index=True)

Identifying common genes across datasets...
Number of common genes across datasets: 1354
Subsetting and appending OSD-47...
Subsetting and appending OSD-48...
Subsetting and appending OSD-137...
Subsetting and appending OSD-168...
Combined RNA-seq data saved with 93 samples and 1354 genes.


In [8]:
# --- Combine all phenotype data into one ---
print("Combining phenotype data across datasets...")

pheno_combined = []

# Standard datasets: 47, 48
for ds in ["47", "48", "137"]:
    if ds in phenotype:
        df = phenotype[ds][["Sample name", "ORO Positivity (%)"]].copy()
        df["Dataset"] = f"OSD-{ds}"
        pheno_combined.append(df)

# Combine all into a single DataFrame
pheno_all = pd.concat(pheno_combined, axis=0, ignore_index=True)

Combining phenotype data across datasets...
Combined phenotype data saved with 57 samples.


In [ ]:
# Strip whitespace to ensure matches
rna_all["Sample name"] = rna_all["Sample name"].str.strip()
pheno_all["Sample name"] = pheno_all["Sample name"].str.strip()

# Find common samples
common_samples = set(rna_all["Sample name"]) & set(pheno_all["Sample name"])
print(f"Number of common samples: {len(common_samples)}")

# Filter both datasets
rna_all = rna_all[rna_all["Sample name"].isin(common_samples)].reset_index(drop=True)
pheno_all = pheno_all[pheno_all["Sample name"].isin(common_samples)].reset_index(drop=True)

In [18]:
def extract_environment(sample_name):
    parts = sample_name.split("_")
    return parts[3] if len(parts) >= 4 else "UNKNOWN"

# Apply to both datasets
rna_all["Environment"] = rna_all["Sample name"].apply(extract_environment)
pheno_all["Environment"] = pheno_all["Sample name"].apply(extract_environment)

In [19]:
rna_all.to_csv("../x_variables/rna_seq-RR1.csv", index=False)
print(f"Combined RNA-seq data saved with {rna_all.shape[0]} samples and {rna_all.shape[1] - 2} genes.")
pheno_all.to_csv("../y_variables/pheno_seq-RR1.csv", index=False)
print(f"Combined phenotype data saved with {pheno_all.shape[0]} samples.")

Combined RNA-seq data saved with 41 samples and 1355 genes.
Combined phenotype data saved with 41 samples.
